In [27]:
# IMPORT STATEMENTS
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import math
import pandas as pd
import scanpy as sc
import os
import GEOparse

In [20]:
# Read raw counts
expr = pd.DataFrame(pd.read_csv('GSE178883_RawCount_Matrix_ann.txt', sep = '\t', header=0))
expr = expr.loc[:,[col for col in expr.columns if (("Neu" in col) or (col in ["GeneID", "gene_sym"]))]]
# Read ih file
ih_df = pd.DataFrame(pd.read_csv('GSE178883-GPL24676-ih.txt', sep = '\t', header=0))
# This is so we can easily rename expr columns to GSM IDs using information in the ih file.
gsm_dict = {ih_df["ClinicalHeader"][i]:ih_df["ArrayID"][i] for i in ih_df.index}
gsm_dict["gene_sym"]="Name"
expr.rename(columns=gsm_dict, inplace=True)
expr

GeneID        Name  GSM5399905  GSM5399906  GSM5399904  \
0      ENSG00000000003      TSPAN6           0           0           0   
1      ENSG00000000005        TNMD           0           0           0   
2      ENSG00000000419        DPM1         482         399         547   
3      ENSG00000000457       SCYL3         177         165         228   
4      ENSG00000000460    C1orf112          74          87          94   
...                ...         ...         ...         ...         ...   
58671  ENSG00000285990  AL589743.7           0           0           0   
58672  ENSG00000285991  AL355312.5           0           0           3   
58673  ENSG00000285992  AC120036.5           0           0           0   
58674  ENSG00000285993  AC018931.1           0           0           0   
58675  ENSG00000285994  AL731559.1          32          27          34   

       GSM5399899  GSM5399900  GSM5399898  GSM5399902  GSM5399903  GSM5399901  
0               4           0           0           1           0           0  
1               0           0           0           0           0           0  
2             264         393         314         280         301         294  
3             237         306         229         199         208         175  
4             116         165         162          99         119         103  
...           ...         ...         ...         ...         ...         ...  
58671           0           0           0           0           0           0  
58672           0           3           0           0           0           0  
58673           0           0           0           0           0           0  
58674           0           0           0           0           0           0  
58675          26          37          13          37          26          24  

[58676 rows x 11 columns]

In [23]:
genes = expr.loc[:,["GeneID", "Name"]]
cols = expr.columns

# Normalize and log transform
expr = expr.drop(['GeneID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
sc.pp.normalize_total(expr, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "GeneID", genes["GeneID"])
expr.columns = cols
expr

# Export to txt
path_dir = "./"
expr.to_csv(path_dir+"GSE178883-GPL24676-expr.txt", header=True, index=False,sep='\t')
expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


GeneID        Name  GSM5399905  GSM5399906  GSM5399904  \
0      ENSG00000000003      TSPAN6    0.000000    0.000000    0.000000   
1      ENSG00000000005        TNMD    0.000000    0.000000    0.000000   
2      ENSG00000000419        DPM1    5.457585    5.209566    5.260299   
3      ENSG00000000457       SCYL3    4.067792    3.989902    4.049519   
4      ENSG00000000460    C1orf112    2.924674    3.145719    2.890361   
...                ...         ...         ...         ...         ...   
58671  ENSG00000285990  AL589743.7    0.000000    0.000000    0.000000   
58672  ENSG00000285991  AL355312.5    0.000000    0.000000    0.268698   
58673  ENSG00000285992  AC120036.5    0.000000    0.000000    0.000000   
58674  ENSG00000285993  AC018931.1    0.000000    0.000000    0.000000   
58675  ENSG00000285994  AL731559.1    1.945246    1.780850    1.731252   

       GSM5399899  GSM5399900  GSM5399898  GSM5399902  GSM5399903  GSM5399901  
0        0.484520    0.000000    0.000000    0.123317    0.000000    0.000000  
1        0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
2        4.773043    4.906538    4.573246    4.699669    4.822770    4.704620  
3        4.623390    4.559153    4.140150    4.229434    4.312204    3.993300  
4        3.652427    3.719457    3.674245    3.297834    3.559899    3.290563  
...           ...         ...         ...         ...         ...         ...  
58671    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
58672    0.000000    0.288439    0.000000    0.000000    0.000000    0.000000  
58673    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
58674    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
58675    1.845703    1.899017    0.959171    2.104920    1.747691    1.607378  

[58676 rows x 11 columns]

In [24]:
# Build idx file

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'GSE178883-GPL24676-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'GSE178883-GPL24676-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx


In [73]:
def printConf(dbid, name):
    path_dir = os.getcwd()
    accessionID = path_dir.split("/")[-1]
    gse = GEOparse.get_GEO(geo=str(accessionID), destdir=path_dir)
    filepath = path_dir+"/"+str(accessionID)+'-%s'%(list(gse.gpls.keys())[0])
    print("[%s]" % dbid)
    print("name = %s" % name)
    print("expr = %s-expr.txt" % filepath)
    print("index = %s-idx.txt" % filepath)
    print("survival = %s-survival.txt" % filepath)
    print("indexHeader = %s-ih.txt" % filepath)
    print("info = %s-info.txt" % filepath)
    print("key = %s" % dbid)
    print("source = %s" % accessionID)
    
def writeConf(dbid, name, key='', cf="/Users/rohan/public_html/Hegemon/explore.conf"):
    path_dir = os.getcwd()
    accessionID = path_dir.split("/")[-1]
    gse = GEOparse.get_GEO(geo=str(accessionID), destdir=path_dir)
    filepath = path_dir+"/"+str(accessionID)+'-%s'%(list(gse.gpls.keys())[0])
    with open(cf, 'a') as f:
        f.write("\n[%s]\n" % dbid)
        f.write("name = %s\n" % name)
        f.write("expr = %s-expr.txt\n" % filepath)
        f.write("index = %s-idx.txt\n" % filepath)
        f.write("survival = %s-survival.txt\n" % filepath)
        f.write("indexHeader = %s-ih.txt\n" % filepath)
        f.write("info = %s-info.txt\n" % filepath)
        f.write("key = %s\n" % key)
        f.write("source = %s\n" % accessionID)

In [74]:
writeConf("NEU3", "Shirakawa 2021 Neutrophil NETosis", key="neu:")

21-Jun-2022 13:33:50 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE178883 already exists. Skipping.
21-Jun-2022 13:33:50 INFO GEOparse - File already exist: using local version.
21-Jun-2022 13:33:50 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE178883/GSE178883_family.soft.gz: 
21-Jun-2022 13:33:50 DEBUG GEOparse - DATABASE: GeoMiame
21-Jun-2022 13:33:50 DEBUG GEOparse - SERIES: GSE178883
21-Jun-2022 13:33:50 DEBUG GEOparse - PLATFORM: GPL24676
21-Jun-2022 13:33:50 DEBUG GEOparse - SAMPLE: GSM5399898
21-Jun-2022 13:33:50 DEBUG GEOparse - SAMPLE: GSM5399899
21-Jun-2022 13:33:50 DEBUG GEOparse - SAMPLE: GSM5399900
21-Jun-2022 13:33:50 DEBUG GEOparse - SAMPLE: GSM5399901
21-Jun-2022 13:33:50 DEBUG GEOparse - SAMPLE: GSM5399902
21-Jun-2022 13:33:50 DEBUG GEOparse - SAMPLE: GSM5399903
21-Jun-2022 13:33:50 DEBUG GEOparse - SAMPLE: GSM5399904
21-Jun-2022 13:33:50 DEBUG GEOparse - SAMPLE: GSM5399905
21-Jun-2022 13:33:50 DEBU